<a href="https://colab.research.google.com/github/alu0101132945/TFG/blob/main/collabBERTTOPIC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [46]:
!pip install --upgrade bertopic

Importamos las librerias necesarias para poder trabajar con el modelo

In [47]:
import requests
import json
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import nltk
from bertopic import BERTopic
from sklearn.feature_extraction.text import CountVectorizer

from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.probability import FreqDist

import string

import re

In [48]:
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
lemmatizer = WordNetLemmatizer()

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [49]:
def tokenize_lowercase(text):
  stop_words = stopwords.words('spanish')

  #add punctuation char's to stopwords list
  stop_words += list(string.punctuation) # <-- contains !"#$%&'()*+,-./:;<=>?@[\]^_`{|}~

  #añadimos los numeros y otras palabras sin valor
  stop_words += ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']
  stop_words += ['xi','sra','sr.','consejero','consejera','legislatura','dirigida', 'presidente','vicepresidente']
  tokens = word_tokenize(text)
  stopwords_removed = [token.lower() for token in tokens if token.lower() not in stop_words]

  return stopwords_removed

In [50]:
def remove_nums(text_object):
  no_nums = list(filter(lambda x: x.isalpha(), text_object))
  return no_nums

In [51]:
def lemmatize_text(df_text):
    lemmatized =[]
    processed = []
    for w in df_text:
        lemmatized.append(lemmatizer.lemmatize(w))
        processed = list(filter(lambda x: x.isalpha(), lemmatized))
    return processed

In [52]:
# guardamos la URL con la info de los grupos
url = "https://parcan.es/api/informacion_grupos/11/"

# Hacemos una petición GET a la API
grupos_resp = requests.get(url)

# Intentar cargar el contenido como JSON
try:
    grupos_json = grupos_resp.json()
    grupos = grupos_json.get('result')

    # Si la carga es exitosa, procede con la extracción de los valores
    id_organo_ids = []

    # Itera sobre cada diccionario en la lista result
    for grupo in grupos:
      id_organo_id = grupo['id_organo_id']
      id_organo_ids.append(id_organo_id)

except json.JSONDecodeError:
    # Si no se puede cargar como JSON, probablemente sea una cadena
    print("El contenido de la respuesta no es un objeto JSON válido.")

In [53]:
base_url = "https://parcan.es/api/informacion_grupos/iniciativas/{}"
urls = [base_url.format(code) for code in id_organo_ids]

In [54]:
extractos = []
for ini_url in urls:
  iniciativas_resp = requests.get(ini_url)
  try:
    iniciativas_json = iniciativas_resp.json()
    iniciativas = iniciativas_json.get('result')
    for iniciativa in iniciativas:
      extracto = iniciativa['extracto']
      extractos.append(extracto)
  except json.JSONDecodeError:
    print("El contenido de la respuesta no es un objeto JSON válido.")
print(extractos)

['el reto demográfico y el equilibrio poblacional en Canarias.', 'la revisión del Régimen Económico y Fiscal de Canarias.', 'Consejo Canario de la Cultura.', 'Grupo Parlamentario Socialista Canario.', 'De la Sra. consejera de Sanidad, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Transición Ecológica y Energía, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Turismo y Empleo, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Universidades, Ciencia e Innovación y Cultura, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Agricultura, Ganadería, Pesca y Soberanía Alimentaria, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Hacienda y Relaciones con la Unión Europea, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Bienestar Social,

In [55]:
extracto_token = []
extracto_tokens = []

# Tokenización y conversión a minúsculas
for extracto in extractos:
  extracto_token.append(tokenize_lowercase(extracto))

# Remoción de números
for i in range(len(extracto_token)):
  extracto_token[i] = remove_nums(extracto_token[i])

# Lematización
for i in range(len(extracto_token)):
  extracto_token[i] = lemmatize_text(extracto_token[i])

# Unir tokens en una cadena y agregar a la lista extracto_tokens
for tokens in extracto_token:
  extracto_tokens.append(" ".join(tokens))

# Imprimir la lista de tokens procesados
print(extracto_tokens)

['reto demográfico equilibrio poblacional canarias', 'revisión régimen económico fiscal canarias', 'consejo canario cultura', 'grupo parlamentario socialista canario', 'sanidad líneas estratégicas desarrollar', 'transición ecológica energía líneas estratégicas desarrollar', 'turismo empleo líneas estratégicas desarrollar', 'universidades ciencia innovación cultura líneas estratégicas desarrollar', 'agricultura ganadería pesca soberanía alimentaria líneas estratégicas desarrollar', 'hacienda relaciones unión europea líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'economía industria comercio autónomos líneas estratégicas desarrollar', 'educación formación profesional actividad física deportes líneas estratégicas desarrollar', 'presidencia administraciones públicas justicia seguridad líneas estratégicas desarrollar', 'hacienda r

In [56]:
import torch
from transformers import DistilBertTokenizer, DistilBertForSequenceClassification

# Load the embedding model
tokenizer = DistilBertTokenizer.from_pretrained('distilbert-base-uncased')
model = DistilBertForSequenceClassification.from_pretrained('distilbert-base-uncased')
topic_model = BERTopic(embedding_model=model, language="spanish", calculate_probabilities=True, verbose=True)

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [57]:
topics, probs = topic_model.fit_transform(extracto_tokens)
hierarchical_topics = topic_model.hierarchical_topics(extracto_tokens)

2024-06-29 20:00:44,300 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/209 [00:00<?, ?it/s]

2024-06-29 20:03:33,653 - BERTopic - Embedding - Completed ✓
2024-06-29 20:03:33,655 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-06-29 20:03:53,543 - BERTopic - Dimensionality - Completed ✓
2024-06-29 20:03:53,545 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-06-29 20:04:00,667 - BERTopic - Cluster - Completed ✓
2024-06-29 20:04:00,676 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-06-29 20:04:00,973 - BERTopic - Representation - Completed ✓
100%|██████████| 129/129 [00:00<00:00, 185.60it/s]


In [58]:
# Asegúrate de que cada elemento en 'topics' sea una lista antes de filtrar
topics_filtered = [[topic for topic in (doc_topics if isinstance(doc_topics, list) else [doc_topics]) if topic not in [-1, 0]] for doc_topics in topics]

# Asegúrate de que 'topics_filtered' no contenga sublistas vacías
topics_filtered = [doc_topics for doc_topics in topics_filtered if doc_topics]

# topics_filtered contiene los índices de los tópicos
topics_words = {topic_num: topic_model.get_topic(topic_num) for doc_topics in topics_filtered for topic_num in doc_topics}
# Convertir los índices de tópicos en palabras clave
topics_words_filtered = [[word for topic_num in doc_topics for word, _ in topics_words[topic_num]] for doc_topics in topics_filtered]


# Continúa con la creación del diccionario y el corpus como antes
dictionary = Dictionary(extracto_token)
corpus = [dictionary.doc2bow(text) for text in extracto_token]

# Asegúrate de que 'topics_words_filtered' no contenga sublistas vacías
topics_words_filtered = [doc_topics for doc_topics in topics_words_filtered if doc_topics]

# Calcula la coherencia con las palabras clave de los tópicos
coherence_model = CoherenceModel(model=topic_model, topics=topics_words_filtered, texts=extracto_token, dictionary=dictionary, coherence='c_v')
coherence = coherence_model.get_coherence()
print(f'Coherencia de los temas con palabras clave para el modelo BERTopic: {coherence}')

[[121], [105], [126], [126], [5], [4], [8], [21], [6], [6], [3], [11], [1], [2], [4], [4], [73], [6], [3], [52], [72], [5], [6], [33], [62], [6], [6], [25], [50], [5], [7], [4], [13], [8], [5], [114], [27], [37], [105], [11], [105], [8], [2], [4], [3], [17], [6], [6], [8], [1], [12], [19], [12], [12], [12], [6], [6], [70], [19], [30], [8], [3], [81], [28], [1], [72], [1], [2], [81], [7], [3], [70], [3], [6], [6], [8], [77], [10], [5], [11], [25], [8], [4], [36], [71], [1], [6], [103], [17], [47], [10], [3], [100], [102], [100], [100], [4], [35], [33], [17], [34], [23], [3], [81], [34], [72], [4], [114], [45], [14], [77], [2], [3], [33], [7], [4], [17], [23], [34], [3], [33], [45], [14], [114], [34], [77], [110], [105], [32], [92], [1], [25], [61], [129], [105], [71], [129], [54], [52], [105], [28], [12], [12], [91], [40], [118], [118], [39], [39], [117], [1], [55], [30], [10], [39], [10], [10], [23], [15], [15], [18], [5], [82], [82], [4], [4], [4], [31], [31], [31], [31], [31], [31], 

Coherencia de los temas con palabras clave para el modelo BERTopic: 0.6236795035160354


In [68]:
from scipy.stats import entropy

# Suponiendo que 'topic_probs' es un array con las probabilidades de cada documento de pertenecer a cada tema
entropias = [entropy(doc_probs) for doc_probs in probs]
diversidad = np.mean(entropias)

print(f"diversidad: {diversidad}")
entropies = [-np.sum(p * np.log(p + 1e-9)) for p in probs]  # +1e-9 para evitar log(0)

# Encuentra la entropía máxima y el documento correspondiente
max_entropy = max(entropies)
max_entropy_document_index = entropies.index(max_entropy)
max_entropy_document = extracto_tokens[max_entropy_document_index]

print(f"Entropía máxima: {max_entropy}")
print(f"Documento con máxima entropía: '{max_entropy_document}'")

diversidad: 2.803427509260644
Entropía máxima: 4.478942031406042
Documento con máxima entropía: 'acciones llevando cabo consejería sanidad servicio canario salud objeto convocar nueva oferta pública empleo garantice calidad servicio público sanitario archipiélago sanidad'


In [73]:
from sklearn.metrics import silhouette_score
# Obtén los embeddings de los documentos
embeddings = topic_model._extract_embeddings(extracto_tokens)
# Calcula el Silhouette Score
score = silhouette_score(embeddings, topics)

print(f"Silhouette Score: {score}")

Silhouette Score: 0.008826063945889473


In [ ]:
topic_model.get_topics()

{-1: [('profesional', 0.011241010844441776),
  ('formación', 0.011086732773121125),
  ('deportes', 0.010901276971016095),
  ('actividad', 0.010753236261888906),
  ('educación', 0.010634277328298724),
  ('física', 0.010579468056742557),
  ('familias', 0.008793782174985552),
  ('social', 0.008707458244867445),
  ('juventud', 0.00864045441781907),
  ('infancia', 0.008427274498792069)],
 0: [('universidades', 0.09979591014387329),
  ('innovación', 0.09630858589317291),
  ('ciencia', 0.09627583213728594),
  ('cultura', 0.0958710203626283),
  ('cultural', 0.017770734548962604),
  ('silbo', 0.013223737552235867),
  ('universitarios', 0.012107942320115387),
  ('investigación', 0.011970409162853623),
  ('canarias', 0.011530703855930828),
  ('expediente', 0.011495055879618759)],
 1: [('vivienda', 0.07507990363390303),
  ('movilidad', 0.06763633870566864),
  ('obras', 0.059856660730314454),
  ('públicas', 0.04456766314440559),
  ('viviendas', 0.019214742916637183),
  ('construcción', 0.0188527824

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=97)

In [ ]:
topic_model.visualize_heatmap(n_clusters=20,width=1000,height=1000)

In [ ]:
topic_model.reduce_topics(extracto_token, nr_topics=30)

TypeError: Make sure that the iterable only contains strings.

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=40)

In [ ]:
topic_model.visualize_barchart(top_n_topics=8)

In [14]:
extractos = {
    'extractos1': [],
    'extractos2': [],
    'extractos3': [],
    'extractos4': [],
    'extractos5': [],
    'extractos6': [],
    'extractos7': []
}
for i, ini_url in enumerate(urls):
    iniciativas_resp = requests.get(ini_url)
    try:
        iniciativas_json = iniciativas_resp.json()
        iniciativas = iniciativas_json.get('result')

        # Obtener el nombre de la variable de extractos
        nombre_variable = f'extractos{i+1}'

        # Obtener la lista de extractos correspondiente
        lista_extractos = extractos[nombre_variable]

        # Agregar extractos a la lista correspondiente
        for iniciativa in iniciativas:
            extracto = iniciativa['extracto']
            lista_extractos.append(extracto)

    except json.JSONDecodeError:
        print("El contenido de la respuesta no es un objeto JSON válido.")
for lista_extractos in extractos.values():
    # Extender la lista de todos_los_extractos con los extractos de la lista actual
    print(lista_extractos)

['el reto demográfico y el equilibrio poblacional en Canarias.', 'la revisión del Régimen Económico y Fiscal de Canarias.', 'Consejo Canario de la Cultura.', 'Grupo Parlamentario Socialista Canario.', 'De la Sra. consejera de Sanidad, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Transición Ecológica y Energía, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Turismo y Empleo, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Universidades, Ciencia e Innovación y Cultura, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Agricultura, Ganadería, Pesca y Soberanía Alimentaria, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Hacienda y Relaciones con la Unión Europea, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Bienestar Social,

In [15]:
extractos_token = {
    'extractos_token1': [],
    'extractos_token2': [],
    'extractos_token3': [],
    'extractos_token4': [],
    'extractos_token5': [],
    'extractos_token6': [],
    'extractos_token7': []
}
for i, extractos_text in enumerate(extractos.values()):
    for extrac in extractos_text:
      # Tokenizar el extracto, eliminar números y lematizar
        extrac_processed = tokenize_lowercase(extrac)
        extrac_processed = remove_nums(extrac_processed)
        extrac_processed = lemmatize_text(extrac_processed)

        # Unir los tokens en una sola cadena
        extrac_processed_str = ' '.join(extrac_processed)

        # Agregar la cadena procesada a la lista correspondiente en extractos_token
        extractos_token[f'extractos_token{i+1}'].append(extrac_processed_str)


for lista_extractos in extractos_token.values():
  # Extender la lista de todos_los_extractos con los extractos de la lista actual
  print(lista_extractos)

['reto demográfico equilibrio poblacional canarias', 'revisión régimen económico fiscal canarias', 'consejo canario cultura', 'grupo parlamentario socialista canario', 'sanidad líneas estratégicas desarrollar', 'transición ecológica energía líneas estratégicas desarrollar', 'turismo empleo líneas estratégicas desarrollar', 'universidades ciencia innovación cultura líneas estratégicas desarrollar', 'agricultura ganadería pesca soberanía alimentaria líneas estratégicas desarrollar', 'hacienda relaciones unión europea líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'economía industria comercio autónomos líneas estratégicas desarrollar', 'educación formación profesional actividad física deportes líneas estratégicas desarrollar', 'presidencia administraciones públicas justicia seguridad líneas estratégicas desarrollar', 'hacienda r

modelo del primer grupo

In [16]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token1'))

2024-06-29 17:07:50,517 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/67 [00:00<?, ?it/s]

2024-06-29 17:08:49,604 - BERTopic - Embedding - Completed ✓
2024-06-29 17:08:49,606 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-06-29 17:09:05,360 - BERTopic - Dimensionality - Completed ✓
2024-06-29 17:09:05,363 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-06-29 17:09:05,727 - BERTopic - Cluster - Completed ✓
2024-06-29 17:09:05,738 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-06-29 17:09:05,882 - BERTopic - Representation - Completed ✓


In [17]:
from gensim.models.coherencemodel import CoherenceModel
from gensim.corpora.dictionary import Dictionary

# Asume que documents es una lista de tus documentos originales
texts = extracto_token
# Asumiendo que 'topics' es una lista de listas o una lista de enteros
# y que deseas filtrar los -1 de las listas internas

# Primero, verifica si 'topics' es una lista de listas o una lista de enteros
if all(isinstance(doc_topics, list) for doc_topics in topics):
    # Si todos los elementos son listas, procede con el filtrado
    topics_filtered = [[topic for topic in doc_topics if topic != -1] for doc_topics in topics]
else:
    # Si hay enteros, conviértelos en listas de un solo elemento o maneja el caso como prefieras
    topics_filtered = [[topic] if isinstance(topic, int) and topic != -1 else topic for topic in topics]

# Asegúrate de que 'topics_filtered' no contenga sublistas vacías
topics_filtered = [doc_topics for doc_topics in topics_filtered if doc_topics]

topics_filtered_clean = [topic if isinstance(topic, list) else [] for topic in topics_filtered if topic != -1]
print(topics_filtered_clean)

# Crea un diccionario de Gensim y un corpus
dictionary = Dictionary(texts)
corpus = [dictionary.doc2bow(text) for text in texts]

# Calcula la coherencia de los temas
coherence_model = CoherenceModel(model=topic_model, topics = topics_filtered_clean ,texts=texts, dictionary=dictionary, coherence='c_v')
coherence = coherence_model.get_coherence()
print(f'Coherencia de los temas para el modelo BERTopic: {coherence}')

[[16], [17], [4], [0], [6], [7], [4], [8], [35], [5], [5], [11], [2], [12], [35], [1], [9], [7], [7], [7], [35], [35], [5], [11], [7], [7], [6], [6], [5], [8], [8], [8], [8], [8], [8], [5], [0], [28], [35], [28], [35], [5], [5], [26], [1], [6], [0], [7], [2], [4], [6], [4], [4], [26], [0], [7], [4], [17], [0], [12], [17], [4], [9], [7], [11], [7], [18], [5], [5], [4], [1], [4], [4], [2], [4], [30], [6], [29], [29], [29], [5], [3], [5], [33], [6], [6], [0], [4], [11], [28], [0], [1], [1], [2], [9], [28], [0], [11], [33], [11], [5], [5], [4], [19], [2], [6], [12], [26], [4], [7], [7], [9], [12], [1], [6], [6], [5], [5], [7], [7], [2], [11], [13], [13], [13], [0], [7], [28], [29], [2], [1], [11], [28], [28], [7], [29], [7], [4], [14], [19], [9], [18], [0], [0], [4], [7], [5], [0], [7], [7], [1], [28], [11], [0], [7], [2], [29], [4], [28], [19], [14], [17], [23], [22], [1], [1], [1], [26], [2], [17], [13], [30], [17], [23], [14], [1], [24], [19], [19], [19], [29], [29], [29], [4], [2], [2]

Coherencia de los temas para el modelo BERTopic: 1.0


In [ ]:
topic_model.get_topic(0)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=20,width=1000,height=1000)

modelo del segundo grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token2'))

In [ ]:
topic_model.get_topic(0)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=15,width=1000,height=1000)

modelo del tercer grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token3'))

In [ ]:
topic_model.get_topic(0)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=13,width=1000,height=1000)

modelo del cuarto grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token4'))

In [ ]:
topic_model.get_topic(0)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=7,width=1000,height=1000)

modelo del quinto grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token5'))

In [ ]:
topic_model.get_topic(0)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=14,width=1000,height=1000)

modelo del sexto grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token6'))

In [ ]:
topic_model.get_topic(0)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=12,width=1000,height=1000)

modelo del septimo grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token7'))

In [ ]:
topic_model.get_topic(0)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=11,width=1000,height=1000)